In [164]:
import numpy as np
import pandas as pd

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio

import json
import geopandas as gpd

In [2]:
with open('GeoJSON/Toronto_fsa.geojson') as f:
  Toronto_fsa = json.load(f)

In [3]:
display(Toronto_fsa["features"][0]['properties'])

{'CFSAUID': 'M9R', 'PRUID': '35', 'PRNAME': 'Ontario'}

In [4]:
display(Toronto_fsa["features"][0]['geometry'])

{'type': 'MultiPolygon',
 'coordinates': [[[[-79.5613053165675, 43.674784800510714],
    [-79.56248600330755, 43.67458759097538],
    [-79.56258440456196, 43.67462479033493],
    [-79.56319650228333, 43.67454019854221],
    [-79.56538430752339, 43.67431338986235],
    [-79.5668485183485, 43.67421159572012],
    [-79.56699098708835, 43.674206590024795],
    [-79.56712701459196, 43.67419749574593],
    [-79.56726348761242, 43.67419289124548],
    [-79.56739951496259, 43.67418379653579],
    [-79.56753548431061, 43.67418380255751],
    [-79.56767188939811, 43.67417918777795],
    [-79.56775419951764, 43.67417110668314],
    [-79.56776878595709, 43.674169699833705],
    [-79.56781029351805, 43.67416559418064],
    [-79.56794739481535, 43.67415199433343],
    [-79.56808459786872, 43.67413840874554],
    [-79.56822138679154, 43.67412478966872],
    [-79.56835820296462, 43.67411119987658],
    [-79.56849539483675, 43.67409321101965],
    [-79.56850057558472, 43.67409269348366],
    [-79.56863

In [5]:
data = pd.read_csv("https://ckan0.cf.opendata.inter.prod-toronto.ca/download_resource/e5bf35bc-e681-43da-b2ce-0242d00922ad?format=csv")
display(data.head())

_id  Assigned_ID Outbreak Associated       Age Group  \
0    1            1            Sporadic  50 to 59 Years   
1    2            2            Sporadic  50 to 59 Years   
2    3            3            Sporadic  20 to 29 Years   
3    4            4            Sporadic  60 to 69 Years   
4    5            5            Sporadic  60 to 69 Years   

      Neighbourhood Name  FSA Source of Infection Classification Episode Date  \
0        Willowdale East  M2N              Travel      CONFIRMED   2020-01-22   
1        Willowdale East  M2N              Travel      CONFIRMED   2020-01-21   
2      Parkwoods-Donalda  M3A              Travel      CONFIRMED   2020-02-05   
3  Church-Yonge Corridor  M4W              Travel      CONFIRMED   2020-02-16   
4  Church-Yonge Corridor  M4W              Travel      CONFIRMED   2020-02-20   

  Reported Date Client Gender   Outcome Currently Hospitalized  \
0    2020-01-23        FEMALE  RESOLVED                     No   
1    2020-01-23          MALE  RESOLVED                     No   
2    2020-02-21        FEMALE  RESOLVED                     No   
3    2020-02-25        FEMALE  RESOLVED                     No   
4    2020-02-26          MALE  RESOLVED                     No   

  Currently in ICU Currently Intubated Ever Hospitalized Ever in ICU  \
0               No                  No                No          No   
1               No                  No               Yes          No   
2               No                  No                No          No   
3               No                  No                No          No   
4               No                  No                No          No   

  Ever Intubated  
0             No  
1             No  
2             No  
3             No  
4             No

In [6]:
data = data[data['FSA'].notna()]

fsa_out = data.groupby(['FSA','Outcome']).size()
display(fsa_out.head())

FSA  Outcome 
M1B  ACTIVE       242
     FATAL         38
     RESOLVED    2648
M1C  ACTIVE       106
     FATAL         75
dtype: int64

In [7]:
count_act = []
count_fat = []
count_res = []

for code in list(data['FSA'].unique()):
    try:
        count_act.append(fsa_out[code]['ACTIVE'])
    except:
        count_act.append(0)
        
for code in list(data['FSA'].unique()):
    try:
        count_fat.append(fsa_out[code]['FATAL'])
    except:
        count_fat.append(0)
        
for code in list(data['FSA'].unique()):
    try:
        count_res.append(fsa_out[code]['RESOLVED'])
    except:
        count_res.append(0)
        
count_act = np.array(count_act)
count_fat = np.array(count_fat)
count_res = np.array(count_res)

total_count = count_act + count_fat + count_res

count_data = pd.DataFrame({'CFSAUID':list(data['FSA'].unique()),'ACTIVE':count_act,'FATAL':count_fat,
                          'RESOLVED':count_res,'TOTAL':total_count})

display(count_data.head())  

CFSAUID  ACTIVE  FATAL  RESOLVED  TOTAL
0     M2N      62     17       756    835
1     M3A      89     12       635    736
2     M4W      13      2       131    146
3     M2R     253     26      1705   1984
4     M1V     148     15      1286   1449

In [206]:
fig = px.choropleth(count_data, geojson=Toronto_fsa, locations='CFSAUID',       
                           color=count_data['FATAL'],
                           color_continuous_scale="viridis_r",
                           featureidkey="properties.CFSAUID",
                           projection="mercator",
                          )

fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

In [17]:
df = data.copy()
df['Reported Date'] = pd.to_datetime(df['Reported Date'])
df = df.set_index('Reported Date')
df['Count'] = 1

In [23]:
daily_data = pd.DataFrame(df['Count'].resample('D').count()).reset_index()
display(daily_data.head())

Reported Date  Count
0    2020-01-23      2
1    2020-01-24      0
2    2020-01-25      0
3    2020-01-26      0
4    2020-01-27      0

In [180]:
fig = px.line(daily_data, x='Reported Date',y='Count',template="simple_white")

fig.update_yaxes(title_text="Total Cases")
fig.update_xaxes(title_text="Date reported")

fig.update_layout(title="Daily case count")

fig.show()

In [37]:
source_data = data.groupby('Source of Infection').size().reset_index(name='Count')
source_data.rename(columns={'Source of Infection':'Source'},inplace=True)
source_data['Source'] = source_data['Source'].replace({'N/A - Outbreak associated':'Outbreak','Unknown/Missing':'Unknown'})
display(source_data.head())

Source  Count
0  Close contact  18921
1      Community   9534
2     Healthcare   2143
3  Institutional   1607
4       Outbreak  13870

In [179]:
fig = px.bar(source_data.query('Source != "Unknown"'), x='Source', y='Count',color = "Count"
             ,color_continuous_scale = 'sunsetdark',text='Count',template="simple_white")

fig.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig.update_yaxes(title_text="Total Cases")
fig.update_xaxes(title_text="Source of Infection")

fig.update_layout(title="Total cases based on source of infection")

fig.show()

In [116]:
df = data[data['Age Group'].notna()]
age_out = df.groupby(['Age Group','Outcome']).size()
display(age_out.head())

Age Group       Outcome 
19 and younger  ACTIVE       878
                FATAL          1
                RESOLVED    9014
20 to 29 Years  ACTIVE      1637
                FATAL          2
dtype: int64

In [118]:
act = np.array([age_out[age]['ACTIVE'] for age in list(df['Age Group'].unique())])
fat = np.array([age_out[age]['FATAL'] for age in list(df['Age Group'].unique())])
res = np.array([age_out[age]['RESOLVED'] for age in list(df['Age Group'].unique())])
tot = act + fat + res
per_fat = 100*fat/tot

Age_data = pd.DataFrame({'Age_Group':list(data['Age Group'].unique()),'Count_resolved':res,'Count_fatal':fat,
                         'Count_active':act,'Total_Count':tot,'Percent_fatal':per_fat})

Age_data = Age_data.reindex([7,1,5,6,0,2,4,3,8])
display(Age_data)

Age_Group  Count_resolved  Count_fatal  Count_active  Total_Count  \
7  19 and younger            9014            1           878         9893   
1  20 to 29 Years           15021            2          1637        16660   
5  30 to 39 Years           12337            4          1272        13613   
6  40 to 49 Years           10480           19          1097        11596   
0  50 to 59 Years           10826           68          1198        12092   
2  60 to 69 Years            6766          207           826         7799   
4  70 to 79 Years            3301          403           428         4132   
3  80 to 89 Years            2864          816           298         3978   
8    90 and older            1677          766           130         2573   

   Percent_fatal  
7       0.010108  
1       0.012005  
5       0.029384  
6       0.163850  
0       0.562355  
2       2.654186  
4       9.753146  
3      20.512821  
8      29.770696

In [215]:
Age_data['Age_Group'].unique()

array(['19 and younger', '20 to 29 Years', '30 to 39 Years',
       '40 to 49 Years', '50 to 59 Years', '60 to 69 Years',
       '70 to 79 Years', '80 to 89 Years', '90 and older'], dtype=object)

In [209]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace(
    go.Bar(x=Age_data['Age_Group'], y=Age_data['Total_Count'], name="Covid Cases Count",marker=dict(
        color=Age_data['Total_Count'],
        colorscale="burg"
    ),text=Age_data['Total_Count']),
    secondary_y=False,
)

fig.update_traces(texttemplate='%{text:.2s}', textposition='inside')

fig.add_trace(
    go.Scatter(x=Age_data['Age_Group'], y=Age_data['Count_fatal'], name="Number of fatal cases",
               line = dict(color='black', width=2)),
    secondary_y=True,
)

fig.update_yaxes(title_text="Total Cases", secondary_y=False)
fig.update_yaxes(title_text="Fatal Cases", secondary_y=True)
fig.update_xaxes(title_text="Age Group")

fig.update_layout(template="simple_white", title="Total and Fatal cases for various Age groups")